In [3]:
!pip install pandas_datareader

     |████████████████████████████████| 109 kB 8.9 MB/s eta 0:00:01


In [1]:
import warnings
warnings.filterwarnings('ignore')

In [2]:
%matplotlib inline

from tqdm import tqdm
from itertools import product
import pandas as pd
import pandas_datareader.data as web
import numpy as np
from numpy.linalg import LinAlgError

import statsmodels.tsa.api as tsa
from statsmodels.graphics.tsaplots import plot_acf, plot_pacf
from statsmodels.tsa.stattools import acf, q_stat, adfuller
from scipy.stats import probplot, moment
from sklearn.metrics import mean_squared_error

import matplotlib.pyplot as plt
import seaborn as sns

In [3]:
sns.set_style('whitegrid')

In [4]:
def plot_correlogram(x, lags=None, title=None):    
    lags = min(10, int(len(x)/5)) if lags is None else lags
    fig, axes = plt.subplots(nrows=2, ncols=2, figsize=(14, 8))
    x.plot(ax=axes[0][0], title='Residuals')
    x.rolling(21).mean().plot(ax=axes[0][0], c='k', lw=1)
    q_p = np.max(q_stat(acf(x, nlags=lags), len(x))[1])
    stats = f'Q-Stat: {np.max(q_p):>8.2f}\nADF: {adfuller(x)[1]:>11.2f}'
    axes[0][0].text(x=.02, y=.85, s=stats, transform=axes[0][0].transAxes)
    probplot(x, plot=axes[0][1])
    mean, var, skew, kurtosis = moment(x, moment=[1, 2, 3, 4])
    s = f'Mean: {mean:>12.2f}\nSD: {np.sqrt(var):>16.2f}\nSkew: {skew:12.2f}\nKurtosis:{kurtosis:9.2f}'
    axes[0][1].text(x=.02, y=.75, s=s, transform=axes[0][1].transAxes)
    plot_acf(x=x, lags=lags, zero=False, ax=axes[1][0])
    plot_pacf(x, lags=lags, zero=False, ax=axes[1][1])
    axes[1][0].set_xlabel('Lag')
    axes[1][1].set_xlabel('Lag')
    fig.suptitle(title, fontsize=14)
    sns.despine()
    fig.tight_layout()
    fig.subplots_adjust(top=.9)

In [5]:
# download series
industrial_production = web.DataReader('IPGMFN', 'fred', '1988', '2017-12').squeeze().dropna()
nasdaq = web.DataReader('NASDAQCOM', 'fred', '1990', '2017-12-31').squeeze().dropna()

In [6]:
# log transformation
nasdaq_log = np.log(nasdaq)
industrial_production_log = np.log(industrial_production)

In [7]:
# differencing
nasdaq_log_diff = nasdaq_log.diff().dropna()

# seasonal differencing => yoy instantanteous returns
industrial_production_log_diff = industrial_production_log.diff(12).dropna()

## Univariate Time Series Models
### Autoregressive (AR) Model
Multiple linear-regression models expressed the variable of interest as a linear combination of predictors or input variables. Univariate time series models relate the value of the time series at the point in time of interest to a linear combination of lagged values of the series and possibly past disturbance terms. While exponential smoothing models are based on a description of the trend and seasonality in the data, ARIMA models aim to describe the autocorrelations in the data. ARIMA(p, d, q) models require stationarity and leverage two building blocks:

- Autoregressive (AR) terms consisting of p-lagged values of the time series
- Moving average (MA) terms that contain q-lagged disturbances

Chapter 8 introduces the ARIMA building blocks, simple autoregressive (AR) and moving average (MA) models, and explains how to combine them in autoregressive moving-average (ARMA) models that may account for series integration as ARIMA models or include exogenous variables as AR(I)MAX models.

Furthermore, we will illustrate how to include seasonal AR and MA terms to extend the toolbox to also include SARMAX models.

### ARMA vs ARIMA
The ARMA model of the undifferenced series produces the same result as the ARIMA model of the differenced series.

In [8]:
model1 = tsa.ARMA(endog=nasdaq_log_diff, order=(2,2)).fit()
model2 = tsa.ARIMA(endog=nasdaq_log, order=(2,1,2)).fit()

/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:581: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  warnings.warn('A date index has been provided, but it has no'


RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =            5     M =           12

At X0         0 variables are exactly at the bounds

At iterate    0    f= -2.82142D+00    |proj g|=  1.43871D-02


 This problem is unconstrained.



At iterate    5    f= -2.82142D+00    |proj g|=  1.61373D-03

At iterate   10    f= -2.82142D+00    |proj g|=  7.36788D-04

At iterate   15    f= -2.82142D+00    |proj g|=  2.03393D-04

At iterate   20    f= -2.82142D+00    |proj g|=  3.18248D-03

At iterate   25    f= -2.82142D+00    |proj g|=  2.36113D-03

At iterate   30    f= -2.82142D+00    |proj g|=  3.37508D-06

At iterate   35    f= -2.82142D+00    |proj g|=  3.62821D-04

At iterate   40    f= -2.82142D+00    |proj g|=  1.75961D-03

At iterate   45    f= -2.82142D+00    |proj g|=  1.41220D-05

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
    5     48     57   

/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:581: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  warnings.warn('A date index has been provided, but it has no'
/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:581: ValueWarning: A date index has been provided, but it has no associated frequency information and so will be ignored when e.g. forecasting.
  warnings.warn('A date index has been provided, but it has no'
 This problem is unconstrained.


RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =            5     M =           12

At X0         0 variables are exactly at the bounds

At iterate    0    f= -2.82142D+00    |proj g|=  1.43871D-02

At iterate    5    f= -2.82142D+00    |proj g|=  1.61373D-03

At iterate   10    f= -2.82142D+00    |proj g|=  7.36788D-04

At iterate   15    f= -2.82142D+00    |proj g|=  2.03393D-04

At iterate   20    f= -2.82142D+00    |proj g|=  3.18248D-03

At iterate   25    f= -2.82142D+00    |proj g|=  2.36113D-03

At iterate   30    f= -2.82142D+00    |proj g|=  3.37508D-06

At iterate   35    f= -2.82142D+00    |proj g|=  3.62821D-04

At iterate   40    f= -2.82142D+00    |proj g|=  1.75961D-03

At iterate   45    f= -2.82142D+00    |proj g|=  1.41220D-05

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = nu

In [9]:
model1.params.sort_index() == model2.params.sort_index().values

ar.L1.NASDAQCOM    True
ar.L2.NASDAQCOM    True
const              True
ma.L1.NASDAQCOM    True
ma.L2.NASDAQCOM    True
dtype: bool

### Seasonal differencing vs SARIMAX
Seasonal differencing has same effect as using SARIMAX w seasonal order (0,1,0,12).

In [12]:
model1 = tsa.statespace.SARIMAX(industrial_production_log, order=(2,0,2), seasonal_order=(0,1,0,12)).fit()
model2 = tsa.statespace.SARIMAX(industrial_production_log_diff, order=(2,0,2), seasonal_order=(0,0,0,12)).fit()

/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
 This problem is unconstrained.

   evaluations in the last line search.  Termination
   may possibly be caused by a bad search direction.
/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS wi

RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =            5     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f= -3.06239D+00    |proj g|=  1.01298D+00

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
    5      3     23      1     0     0   7.137D-02  -3.062D+00
  F =  -3.0624160245709970     

CONVERGENCE: REL_REDUCTION_OF_F_<=_FACTR*EPSMCH             
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =            5     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f= -3.1

 This problem is unconstrained.


In [13]:
model1.params.to_frame('SARIMAX').join(model2.params.to_frame('diff'))

SARIMAX      diff
ar.L1   1.761184  1.761184
ar.L2  -0.783701 -0.783701
ma.L1  -0.840799 -0.840799
ma.L2   0.314827  0.314827
sigma2  0.000103  0.000103

## Finding the optimal ARMA lags
### Run candidate models
We iterate over various (p, q) lag combinations and collect diagnostic statistics to compare the result.

In [14]:
train_size = 120
results = {}
y_true = industrial_production_log_diff.iloc[train_size:]
for p in range(5):
    for q in range(5):
        aic, bic = [], []
        if p == 0 and q == 0:
            continue
        print(p, q)
        convergence_error = stationarity_error = 0
        y_pred = []
        for T in range(train_size, len(industrial_production_log_diff)):
            train_set = industrial_production_log_diff.iloc[T-train_size:T]
            try:
                model = tsa.ARMA(endog=train_set, order=(p, q)).fit()
            except LinAlgError:
                convergence_error += 1
            except ValueError:
                stationarity_error += 1

            forecast, _, _ = model.forecast(steps=1)
            y_pred.append(forecast[0])
            aic.append(model.aic)
            bic.append(model.bic)

        result = (pd.DataFrame({'y_true': y_true, 'y_pred': y_pred})
                  .replace(np.inf, np.nan)
                  .dropna())

        rmse = np.sqrt(mean_squared_error(
            y_true=result.y_true, y_pred=result.y_pred))

        results[(p, q)] = [rmse,
                           np.mean(aic),
                           np.mean(bic),
                           convergence_error,
                           stationarity_error]

0 1
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =            2     M =           12

At X0         0 variables are exactly at the bounds

At iterate    0    f= -2.48712D+00    |proj g|=  4.87634D-01

At iterate    5    f= -2.48730D+00    |proj g|=  1.02979D-01

At iterate   10    f= -2.48781D+00    |proj g|=  2.00773D-01

At iterate   15    f= -2.48784D+00    |proj g|=  2.66454D-06

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
    2     17     26      1     0     0   2.087D-06  -2.488D+00
  F =  -2.4878401745823662     

CONVERGENCE: REL_REDUCTION_OF_F_<=_FACTR*EPSMCH             
RUNN

/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
 This problem is unconstrained.
/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
 This problem is unconstrained.
/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
 This problem is unconstrained.
/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency i


At iterate    5    f= -2.49788D+00    |proj g|=  1.50988D-01

At iterate   10    f= -2.49871D+00    |proj g|=  2.32606D-01

At iterate   15    f= -2.49874D+00    |proj g|=  1.82077D-06

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
    2     16     21      1     0     0   4.441D-08  -2.499D+00
  F =  -2.4987440863984873     

CONVERGENCE: REL_REDUCTION_OF_F_<=_FACTR*EPSMCH             
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =            2     M =           12

At X0         0 variables are exactly at the bounds

At iterate    0    f= -2.50408D+00    |proj g|=  3.25581D-01

At iter

/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
 This problem is unconstrained.
/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
 This problem is unconstrained.
/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
 This problem is unconstrained.
/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency i


At iterate   10    f= -2.50777D+00    |proj g|=  6.82685D-01

At iterate   15    f= -2.50920D+00    |proj g|=  5.71987D-05

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
    2     17     21      1     0     0   2.487D-06  -2.509D+00
  F =  -2.5092003256317725     

CONVERGENCE: REL_REDUCTION_OF_F_<=_FACTR*EPSMCH             
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =            2     M =           12

At X0         0 variables are exactly at the bounds

At iterate    0    f= -2.50457D+00    |proj g|=  6.20557D-01

At iterate    5    f= -2.50484D+00    |proj g|=  1.56462D-01

At iter

...

RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =            9     M =           12

At X0         0 variables are exactly at the bounds

At iterate    0    f= -3.20711D+00    |proj g|=  1.71313D-01

At iterate    5    f= -3.23280D+00    |proj g|=  7.92205D-02

At iterate   10    f= -3.24196D+00    |proj g|=  3.87355D-02

At iterate   15    f= -3.24735D+00    |proj g|=  1.19574D-01

At iterate   20    f= -3.25017D+00    |proj g|=  3.42771D-02

At iterate   25    f= -3.25348D+00    |proj g|=  6.59668D-03


 This problem is unconstrained.



At iterate   30    f= -3.25362D+00    |proj g|=  2.43094D-04

At iterate   35    f= -3.25362D+00    |proj g|=  9.32587D-07

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
    9     37     50      1     0     0   7.550D-07  -3.254D+00
  F =  -3.2536248076559220     

CONVERGENCE: REL_REDUCTION_OF_F_<=_FACTR*EPSMCH             


/home/jongoon/anaconda3/lib/python3.8/site-packages/statsmodels/tsa/base/tsa_model.py:524: ValueWarning: No frequency information was provided, so inferred frequency MS will be used.
  warnings.warn('No frequency information was'
 This problem is unconstrained.


RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =            9     M =           12

At X0         0 variables are exactly at the bounds

At iterate    0    f= -3.21070D+00    |proj g|=  1.69800D-02

At iterate    5    f= -3.21170D+00    |proj g|=  5.71562D-02

At iterate   10    f= -3.21210D+00    |proj g|=  5.69766D-02

At iterate   15    f= -3.21448D+00    |proj g|=  2.69404D-01

At iterate   20    f= -3.22108D+00    |proj g|=  2.12119D-01

At iterate   25    f= -3.22915D+00    |proj g|=  1.09206D-01

At iterate   30    f= -3.23931D+00    |proj g|=  2.58699D-01

At iterate   35    f= -3.25319D+00    |proj g|=  2.42517D-02

At iterate   40    f= -3.25366D+00    |proj g|=  1.39613D-02

At iterate   45    f= -3.25371D+00    |proj g|=  1.01857D-02

At iterate   50    f= -3.25375D+00    |proj g|=  2.17963D-03

At iterate   55    f= -3.25377D+00    |proj g|=  5.32623D-03

At iterate   60    f= -3.25388D+00    |proj g|=  5.90270D-03

At iterate   65    f= -3.2

In [15]:
arma_results = pd.DataFrame(results).T
arma_results.columns = ['RMSE', 'AIC', 'BIC', 'convergence', 'stationarity']
arma_results.index.names = ['p', 'q']
arma_results.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 24 entries, (0, 1) to (4, 4)
Data columns (total 5 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   RMSE          24 non-null     float64
 1   AIC           24 non-null     float64
 2   BIC           24 non-null     float64
 3   convergence   24 non-null     float64
 4   stationarity  24 non-null     float64
dtypes: float64(5)
memory usage: 1.5 KB


In [16]:
with pd.HDFStore('arima.h5') as store:
    store.put('arma', arma_results)

In [17]:
# We aim to minimize both RMSE and BIC:
arma_results.nsmallest(5, columns=['RMSE'])

RMSE         AIC         BIC  convergence  stationarity
p q                                                             
4 0  0.010115 -755.840103 -739.115153          0.0           0.0
  1  0.010120 -756.295011 -736.782569          0.0           2.0
3 0  0.010651 -745.020841 -731.083383          0.0           0.0
  3  0.011280 -756.366203 -734.066269          3.0          13.0
  1  0.011344 -751.800424 -735.075474          0.0           5.0